In [1]:
from bokeh.plotting import show, figure, output_notebook
from bokeh.models.widgets import RadioGroup, Button
from bokeh.layouts import row
from random import random
import numpy as np
import time
import math

output_notebook()

Loading BokehJS ...

In [2]:
vertices = np.matrix([
    [-0.5, -0.5, -0.5],
    [0.5, -0.5, -0.5],
    [0.5, 0.5, -0.5],
    [-0.5, 0.5, -0.5],
    [-0.5, -0.5, 0.5],
    [0.5, -0.5, 0.5],
    [0.5, 0.5, 0.5],
    [-0.5, 0.5, 0.5],
])

In [3]:
def projection_2D(vertices=vertices):
    return projection_matrix.dot(vertices.T).T

In [4]:
def rotate(thetaX=0, thetaY=0, thetaZ=0, vertices=vertices):
    
    sin = math.sin(thetaX);
    cos = math.cos(thetaX);
    
    rotateX = np.matrix([
        [1, 0, 0],
        [0, cos, -sin],
        [0, sin, cos],
    ])
    
    sin = math.sin(thetaY);
    cos = math.cos(thetaY);
    
    rotateY = np.matrix([
        [cos, 0, sin],
        [0, 1, 0],
        [-sin, 0, cos],
    ])
    
    sin = math.sin(thetaZ);
    cos = math.cos(thetaZ);
    
    rotateZ = np.matrix([
        [cos, -sin, 0],
        [sin, cos, 0],
        [0, 0, 1]
    ])
        
    return vertices.dot(rotateX.dot(rotateY.dot(rotateZ)))

In [5]:
def scale(s=1, vertices=vertices):
    return vertices * s

In [6]:
def translate(dx=0, dy=0, dz=0, vertices=vertices):
    return vertices + np.matrix([
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz],
        [dx, dy, dz]
    ])

In [7]:
def draw(vertices=vertices):
    vertices = rotate(thetaX=1,thetaY=1,thetaZ=1,vertices=vertices)
    projection = projection_2D(vertices)
    
    for i in range(len(edges)):
        point1 = projection[edges[i][0]]
        point2 = projection[edges[i][1]]
        
        cube[i].data_source.data = {
            'x':[point1[0, 0],point2[0, 0]],
            'y':[point1[0, 1],point2[0, 1]]
        }

In [8]:
def hitWall(vertices=vertices, rotateAngle=0, scaleSize=1, translateAngle=(1, 1)):
    x_max = float("-inf")
    x_min = float("inf")
    y_max = float("-inf")
    y_min = float("inf")
    
    for ptr in cube:
        
        x_min = min(x_min, ptr.data_source.data['x'][0], ptr.data_source.data['x'][1])
        y_min = min(y_min, ptr.data_source.data['y'][0], ptr.data_source.data['y'][1])
        
        x_max = max(x_max, ptr.data_source.data['x'][0], ptr.data_source.data['x'][1])
        y_max = max(y_max, ptr.data_source.data['y'][0], ptr.data_source.data['y'][1])
    
    center = [(x_max + x_min)/2, (y_max + y_min)/2]
    ctr.data_source.data = {'x':[center[0]],'y':[center[1]]}
    
    angle_x = translateAngle[0]
    angle_y = translateAngle[1]
    
    if center[0]<0:
        angle_y = 1
    if center[0]>10:
        angle_y = -1
    if center[1]<0:
        angle_x = -1
    if center[1]>10:
        angle_x = 1
        
    translateAngle = (angle_x, angle_y)
    return (rotateAngle, scaleSize, translateAngle)

In [9]:
def animate():
    rotated_vertices=vertices
    
    rotateAngle = 0.005
    scaleSize = 1
    scaleFector = 1.002
    translateAngle = (-1,1)

    x = 0
    y = 0
    
    for j in range(0, 2000):
        
        x = x + translateAngle[0]
        y = y + translateAngle[1]

        rotated_vertices = rotate(
            thetaX=rotateAngle, 
            thetaY=rotateAngle, 
            thetaZ=rotateAngle, 
            vertices=rotated_vertices
        )
        
        scaled_vertices = scale(s=scaleSize, vertices=rotated_vertices)     
        draw_vertices = translate(dx=x/25, dy=y/25, dz=0, vertices=scaled_vertices) 
        draw(vertices = draw_vertices)

        rotateAngle, scaleSize, translateAngle = hitWall(
            vertices = draw_vertices, 
            rotateAngle = rotateAngle,
            scaleSize = scaleSize,
            translateAngle = translateAngle
        )
        
        if scaleSize > 2:
            scaleFector = 0.998
        
        if scaleSize < 1:
            scaleFector = 1.002
        
        scaleSize *= scaleFector
        time.sleep(0.001)

In [10]:
def handler(doc):
    doc.add_root(row(f,start_but))

In [11]:
f = figure(
    x_range = (-1, 11),
    y_range = (-1, 11),
    plot_width = 500,
    plot_height = 500
)

f.line([0,10,10,0,0],[0,0,10,10,0])
ctr = f.scatter(x=[0],y=[0])

cube = []
for i in range(0, 12):
    cube.append(f.line([],[]))

projection_matrix = np.matrix([
    [1, 0 ,0],
    [0, 1 ,0]
]) 

edges = [
    [0, 1], [1, 2], [2, 3], [3, 0],
    [4, 5], [5, 6], [6, 7], [7, 4],
    [0, 4], [1, 5], [2, 6], [3, 7]
]

start_but = Button(label="Start", button_type="success")
start_but.on_click(animate)   

draw()
show(handler)